# Imports

In [62]:
! pip install pymongo
import pymongo
import pandas as pd

from google.colab import userdata
from bson.dbref import DBRef

# Connecting to MongoDB

In [63]:
client = pymongo.MongoClient(userdata.get('MONGO_CONN_STR'))

try:
  client.admin.command('ping')
  print("Pinged your deployment. You successfully connected to MongoDB!")
except Exception as e:
  print('Failed to connect: ' + e)

Pinged your deployment. You successfully connected to MongoDB!


## Setting up database

In [64]:
db = client['spotifyDatabase']

tracks = db['tracks']
genres = db['genres']
artists = db['artists']

Data aquisition

In [65]:
df = pd.read_csv("hf://datasets/maharshipandya/spotify-tracks-dataset/dataset.csv")

df


Unnamed: 0                track_id                 artists  \
0                0  5SuOikwiRyPMVoIQDJUgSV             Gen Hoshino   
1                1  4qPNDBW1i3p13qLCt0Ki3A            Ben Woodward   
2                2  1iJBSr7s7jYXzM8EGcbK5b  Ingrid Michaelson;ZAYN   
3                3  6lfxq3CG4xtTiEg7opyCyx            Kina Grannis   
4                4  5vjLSffimiIP26QG5WcN2K        Chord Overstreet   
...            ...                     ...                     ...   
113995      113995  2C3TZjDRiAzdyViavDJ217           Rainy Lullaby   
113996      113996  1hIz5L4IB9hN3WRYPOCGPw           Rainy Lullaby   
113997      113997  6x8ZfSoqDjuNa5SVP5QjvX           Cesária Evora   
113998      113998  2e6sXL2bYv4bSz6VTdnfLs        Michael W. Smith   
113999      113999  2hETkH7cOfqmz3LqZDHZf5           Cesária Evora   

                                               album_name  \
0                                                  Comedy   
1                                        Ghost (Acoustic)   
2                                          To Begin Again   
3       Crazy Rich Asians (Original Motion Picture Sou...   
4                                                 Hold On   
...                                                   ...   
113995  #mindfulness - Soft Rain for Mindful Meditatio...   
113996  #mindfulness - Soft Rain for Mindful Meditatio...   
113997                                            Best Of   
113998                                  Change Your World   
113999                                     Miss Perfumado   

                        track_name  popularity  duration_ms  explicit  \
0                           Comedy          73       230666     False   
1                 Ghost - Acoustic          55       149610     False   
2                   To Begin Again          57       210826     False   
3       Can't Help Falling In Love          71       201933     False   
4                          Hold On          82       198853     False   
...                            ...         ...          ...       ...   
113995         Sleep My Little Boy          21       384999     False   
113996            Water Into Light          22       385000     False   
113997              Miss Perfumado          22       271466     False   
113998                     Friends          41       283893     False   
113999                   Barbincor          22       241826     False   

        danceability  energy  ...  loudness  mode  speechiness  acousticness  \
0              0.676  0.4610  ...    -6.746     0       0.1430        0.0322   
1              0.420  0.1660  ...   -17.235     1       0.0763        0.9240   
2              0.438  0.3590  ...    -9.734     1       0.0557        0.2100   
3              0.266  0.0596  ...   -18.515     1       0.0363        0.9050   
4              0.618  0.4430  ...    -9.681     1       0.0526        0.4690   
...              ...     ...  ...       ...   ...          ...           ...   
113995         0.172  0.2350  ...   -16.393     1       0.0422        0.6400   
113996         0.174  0.1170  ...   -18.318     0       0.0401        0.9940   
113997         0.629  0.3290  ...   -10.895     0       0.0420        0.8670   
113998         0.587  0.5060  ...   -10.889     1       0.0297        0.3810   
113999         0.526  0.4870  ...   -10.204     0       0.0725        0.6810   

        instrumentalness  liveness  valence    tempo  time_signature  \
0               0.000001    0.3580   0.7150   87.917               4   
1               0.000006    0.1010   0.2670   77.489               4   
2               0.000000    0.1170   0.1200   76.332               4   
3               0.000071    0.1320   0.1430  181.740               3   
4               0.000000    0.0829   0.1670  119.949               4   
...                  ...       ...      ...      ...             ...   
113995          0.928000    0.0863   0.0339  125.995               5   
113996          0.97

Data cleaning

In [66]:
initial_rows = len(df)
df = df.dropna()
rows_removed = initial_rows - len(df)
print(f"{rows_removed} rows removed.")

if 'Unnamed: 0' in df.columns:
  df = df.drop(columns=['Unnamed: 0'])
  print("Unnamed column removed successfully.")
else:
  print("No unnamed column found in the DataFrame.")


1 rows removed.


Creating dataframe of individual artists

In [67]:

artists_df = df['artists'].str.split(';').explode().reset_index(drop=True)

# Remove duplicates and convert to DataFrame
artists_df = pd.DataFrame(artists_df.unique(), columns=['artist'])

# Display the resulting DataFrame
artists_df


artist
0                               Gen Hoshino
1                              Ben Woodward
2                         Ingrid Michaelson
3                                      ZAYN
4                              Kina Grannis
...                                     ...
29854             The WRLDFMS Tony Williams
29855                            John Wilds
29856                          Molly Skaggs
29857  Cuencos Tibetanos Sonidos Relajantes
29858                           Brock Human

[29859 rows x 1 columns]

# Database injection

- insert artists and map their id to their string name
- insert genres and map their id to their string name
- parse artists from tracks and replace their strings with id references
- same thing for genres
- insert the tracks to the database

In [68]:
# Create a dictionary to map artist names to their corresponding MongoDB IDs
artist_name_to_id = {}

# Insert each unique artist into the 'artists' collection and store the mapping
for index, row in artists_df.iterrows():
    artist_name = row['artist']
    if artist_name not in artist_name_to_id:
        result = artists.insert_one({'artist': artist_name})
        artist_name_to_id[artist_name] = result.inserted_id
        print(f"Inserted artist: {artist_name} ({index}/{len(artists_df)})")
    else:
        print(f"Skipping duplicate artist: {artist_name} ({index}/{len(artists_df)})")

genres_df = df['track_genre'].unique()
genre_name_to_id = {}

for genre_name in genres_df:
    if genre_name not in genre_name_to_id:
      result = genres.insert_one({'genre': genre_name})
      genre_name_to_id[genre_name] = result.inserted_id

# Preprocess the DataFrame
def preprocess_data(row):
    artist_refs = []
    for artist_name in row['artists'].split(';'):
      if artist_name in artist_name_to_id:
        artist_refs.append(DBRef('artists', artist_name_to_id[artist_name]))
      else:
        # Handle cases where artist is not found
        print(f"Warning: Artist '{artist_name}' not found in the database.")

    genre_ref = DBRef('genres', genre_name_to_id[row['track_genre']])
    if genre_ref is None:
        print(f"Warning: Genre '{row['track_genre']}' not found in the database.")

    track_data = {
        'track_id': row['track_id'],
        'artists': artist_refs,
        'track_genre': genre_ref,
    }

    for column in df.columns:
        if column not in ['track_id', 'artists', 'track_genre']:
            track_data[column] = row[column]

    return track_data

preprocessed_data = df.apply(preprocess_data, axis=1).to_list()

# Insert the preprocessed data into the 'tracks' collection
tracks.insert_many(preprocessed_data)


Streaming output truncated to the last 5000 lines.
Inserted artist: Silent Child (24859/29859)
Inserted artist: gavn! (24860/29859)
Inserted artist: Sik World (24861/29859)
Inserted artist: Jbrisko (24862/29859)
Inserted artist: Traap (24863/29859)
Inserted artist: wonder (24864/29859)
Inserted artist: Killval (24865/29859)
Inserted artist: Prompto (24866/29859)
Inserted artist: Lofi Temptation (24867/29859)
Inserted artist: Arden Jones (24868/29859)
Inserted artist: Slipfunc (24869/29859)
Inserted artist: Kren (24870/29859)
Inserted artist: Ayleen Valentine (24871/29859)
Inserted artist: Rozei (24872/29859)
Inserted artist: Chloe Sagum (24873/29859)
Inserted artist: Lil Rae (24874/29859)
Inserted artist: sammy rash (24875/29859)
Inserted artist: KillBunk (24876/29859)
Inserted artist: KevGee (24877/29859)
Inserted artist: sleep.ing (24878/29859)
Inserted artist: EGOVERT (24879/29859)
Inserted artist: Thekidszn (24880/29859)
Inserted artist: Dro Kenji (24881/29859)
Inserted artist: Mik

InsertManyResult([ObjectId('67d107d3e2930e01b8c8186f'), ObjectId('67d107d3e2930e01b8c81870'), ObjectId('67d107d3e2930e01b8c81871'), ObjectId('67d107d3e2930e01b8c81872'), ObjectId('67d107d3e2930e01b8c81873'), ObjectId('67d107d3e2930e01b8c81874'), ObjectId('67d107d3e2930e01b8c81875'), ObjectId('67d107d3e2930e01b8c81876'), ObjectId('67d107d3e2930e01b8c81877'), ObjectId('67d107d3e2930e01b8c81878'), ObjectId('67d107d3e2930e01b8c81879'), ObjectId('67d107d3e2930e01b8c8187a'), ObjectId('67d107d3e2930e01b8c8187b'), ObjectId('67d107d3e2930e01b8c8187c'), ObjectId('67d107d3e2930e01b8c8187d'), ObjectId('67d107d3e2930e01b8c8187e'), ObjectId('67d107d3e2930e01b8c8187f'), ObjectId('67d107d3e2930e01b8c81880'), ObjectId('67d107d3e2930e01b8c81881'), ObjectId('67d107d3e2930e01b8c81882'), ObjectId('67d107d3e2930e01b8c81883'), ObjectId('67d107d3e2930e01b8c81884'), ObjectId('67d107d3e2930e01b8c81885'), ObjectId('67d107d3e2930e01b8c81886'), ObjectId('67d107d3e2930e01b8c81887'), ObjectId('67d107d3e2930e01b8c818

# Query Testing

- first 10 artists
- first 10 genres

In [69]:
# Query the first 10 rows of the artists collection
results = artists.find().limit(10)

# Iterate through the results and print information about each artist
print("Artists:")
for artist in results:
  print(artist)

print('Genres:')
for genre in genres.find().limit(10):
  print(genre)


Artists:
{'_id': ObjectId('67d10219e2930e01b8c7a35a'), 'artist': 'Gen Hoshino'}
{'_id': ObjectId('67d10219e2930e01b8c7a35b'), 'artist': 'Ben Woodward'}
{'_id': ObjectId('67d10219e2930e01b8c7a35c'), 'artist': 'Ingrid Michaelson'}
{'_id': ObjectId('67d10219e2930e01b8c7a35d'), 'artist': 'ZAYN'}
{'_id': ObjectId('67d10219e2930e01b8c7a35e'), 'artist': 'Kina Grannis'}
{'_id': ObjectId('67d10219e2930e01b8c7a35f'), 'artist': 'Chord Overstreet'}
{'_id': ObjectId('67d10219e2930e01b8c7a360'), 'artist': 'Tyrone Wells'}
{'_id': ObjectId('67d10219e2930e01b8c7a361'), 'artist': 'A Great Big World'}
{'_id': ObjectId('67d10219e2930e01b8c7a362'), 'artist': 'Christina Aguilera'}
{'_id': ObjectId('67d10219e2930e01b8c7a363'), 'artist': 'Jason Mraz'}
Genres:
{'_id': ObjectId('67d107cbe2930e01b8c817fd'), 'genre': 'acoustic'}
{'_id': ObjectId('67d107cbe2930e01b8c817fe'), 'genre': 'afrobeat'}
{'_id': ObjectId('67d107cbe2930e01b8c817ff'), 'genre': 'alt-rock'}
{'_id': ObjectId('67d107cbe2930e01b8c81800'), 'genre'